In [1]:
import warnings
warnings.filterwarnings("ignore")
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

### Dashapp to display implied volatility vs time and price using a constant underlying price
* **This requires plotly 4.0 or greater** *

Calculate the implied volatility of each days options as if the underlying futures contract were always some fixed value. For example, if the actual futures is 100, make that price 50, and then change all of the strike prices so that the strike prices are relative to the value 50.  

1. The 100 call would be a 50 dollar call.  
2. The 95 put would be a 45 dollar put.  
3. The 105 call would be a 55 dollar call


In [2]:
import pandas as pd
import numpy as np

import sys
import os
if  not './' in sys.path:
    sys.path.append('./')
if  not '../' in sys.path:
    sys.path.append('../')

import plotly.graph_objs as go
from plotly.offline import  init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.tools as tls
from plotly.subplots import make_subplots
from plotly.graph_objs.layout import Font,Margin
from IPython import display

import datetime
from tqdm import tqdm,tqdm_notebook
from dashapp import dashapp2 as dashapp
import dash_html_components as html
import dash_core_components as dcc
import pyarrow as pa
import redis
import pdb

In [3]:
redis_port = 6379
redis_db = redis.Redis(host = 'localhost',port=6379,db=0)

In [4]:
def get_redis_df(key):
    context = pa.default_serialization_context()
    df = context.deserialize(redis_db.get(key))
    return df

### Show graphs

In [5]:
commod = 'CL'
year = 2020
cols = ['settle_date','iv','fprice']
df_cuv_implied = get_redis_df('df_cuv_implied')
symbols = df_cuv_implied[df_cuv_implied.symbol.str.slice(0,2)==commod].symbol.unique()
symbols = [s for s in symbols if int(s[-2:])+2000 == year]
for symbol in [k for k in symbols]:
    df_to_graph = df_cuv_implied[df_cuv_implied.symbol==symbol].iloc[:-1][cols]
    fig = dashapp.plotly_plot(
        df_in=df_to_graph,x_column='settle_date',yaxis2_cols=['fprice'],
        y_left_label='Implied Volatility',y_right_label='Futures Close',
        plot_title=f"{symbol} Pseudo-Volatility vs Price"
    )
    iplot(fig)


### Methods to create dashapp

In [6]:
def make_page_title(title_text,div_id=None,html_container=None,parent_class=None,
                   panel_background_color='#CAE2EB'):
    par_class = parent_class
    if par_class is None:
        par_class = dashapp.pnnm
    htmc = html_container
    if htmc is None:
        htmc = html.H2
        
    title_parts = title_text.split('\n')
    

    title_list = [htmc(tp,className=dashapp.pnncnm) for tp in title_parts]
    r = dashapp.multi_row_panel(title_list,
                 parent_class=par_class,
                 div_id=div_id,
                 panel_background_color=panel_background_color) 
    return r   


In [65]:
_create_dropdown_callback = lambda df,comp_id,col,init_value,multi: dashapp.make_dropdown(
            df,comp_id,col,current_value=init_value,multi=multi)

_inputbox_style = {"font-size":"18px","text-align":"center","position":"relative",
    "display":"inline-block","width":"130px","height":"45px"}
def _create_inputbox_callback(df,comp_id,col,init_value,multi=None): 
    inputbox = dcc.Input(
        id='comp_id',value=init_value,
        style=_inputbox_style,debounce=True,step=.001
    )    
    
    
# def components_from_df(df,columns,d_prefix,init_values=None,multi=False,
#                       create_component_callback=None):
#     ccc = _create_dropdown_callback
#     if create_component_callback is not None:
#         ccc = create_component_callback
def components_from_df(df,columns,d_prefix,init_values=None,multi=False):
    dict_component = {}
    for i in range(len(columns)):
        col = columns[i]
        init_value = None if init_values is None else init_values[i]
        if multi:
            init_value = [init_value]
        comp_id = f"{d_prefix}_{col}"
        comp = _create_dropdown_callback(
            df,comp_id,col,init_value,multi)
        dict_component[col] = comp
    return dict_component        
        


In [66]:
_query_operators_options = [
    {'label':'','value':''},
    {'label':'=','value':'=='},
    {'label':'!=','value':'!='},
    {'label':'>','value':'>'},
    {'label':'<','value':'<'},
    {'label':'>=','value':'>='},
    {'label':'<=','value':'<='},
    {'label':'free','value':''},
] 

class FilterDfComponent(html.Div):
    def __init__(self,comp_id,col,text=None):
        super(FilterDfComponent,self).__init__(id=comp_id)
        self.col = col
        div_text = col if text is None else text
        self.col_div = dashapp.make_text_centered_div(div_text)
        dd_id = f"ddop_{comp_id}"
        self.operator_dd = dcc.Dropdown(id=dd_id,options=_query_operators_options,value='')
        input_id = f"inputop_{comp_id}"
        self.operand_input = dcc.Input(id=input_id,value='',debounce=True)
        
        mcp =  dashapp.multi_column_panel(
            [self.col_div,self.operator_dd,self.operand_input],
            grid_template='1fr 1fr 1fr'
        )
        self.children = mcp#.children
        
class _FilterDescriptor():
    def __init__(self,column,init_value,text):
        self.column=column
        self.init_value=init_value
        self.text=text



In [67]:
def create_dashtable_page(
    df,
    dt_id,
    filter_dd_list,
    get_data_callback,
    multi=False,
    loading_full_screen=True,
    title=None):
    
#     dd_prefix = f"{dt_id}_dd_"
    filter_columns = [fdd.column for fdd in filter_dd_list]
    init_values = [fdd.init_value for fdd in filter_dd_list]
    text_values = [fdd.text for fdd in filter_dd_list]
    filter_components = [FilterDfComponent(f"{dt_id}_{[fdd.column]}_fc",fdd.column,fdd.text) for fdd in filter_dd_list]
    
    
    data_store = dcc.Store(id=f'{dt_id}_data_store')
    data_store_loading = dcc.Loading(
        id='data_store_loading',children=[data_store],fullscreen=loading_full_screen)
    
    # callback to populate data_store's dataframe
    id_df = f'df_{dt_id}'
    def _filter_data(input_data):
        df = get_data_callback()
        # Get len of input_data array.  
        # Half of that array are from dcc.Inputs that you 
        #   specify in the input_tuple_list argument to the DashLink constructor.
        # The other half of that array are from dcc.Dropdowns that you
        #   specify in the state_tuple_list argument to the DashLink constructor.
        input_data_len = len(input_data)
        num_inputs = int(input_data_len/2)
        for i in range(num_inputs):
            dropdown_value = input_data[i+num_inputs]
            if dropdown_value == '':
                continue
            input_value = input_data[i]
            if (input_value is not None) and (dropdown_value is not None):
                col = filter_columns[i]
                # see if col is numeric
                needs_quotes = False
                try:
                    colsum = df[col].astype(float).sum()
                except:
                    needs_quotes = True
                ipv = "''" if input_value is None else input_value
                ipv = f"'{ipv}'" if needs_quotes else ipv
                filter_query = f"{col} {dropdown_value} {ipv}"
                print(f"_filter_query: {filter_query}")
                df = df.query(filter_query)
        return [{id_df:df.to_dict('rows')}]
    
    filter_inputs = [(fc.operand_input,'value') for fc in filter_components]
    filter_dropdowns = [(fc.operator_dd,'value') for fc in filter_components]
    
    data_store_link = dashapp.DashLink(
        filter_inputs,[(data_store,'data')],
        io_callback=_filter_data,
        state_tuple_list=filter_dropdowns
    )
    
    # create dashtable, using the data_store
    iv_list = init_values if init_values is not None else [None for _ in filter_columns]
    df_init = get_data_callback()
    dt_values,dt_nav_link = dashapp.make_dashtable(
        dt_id,df_in=df_init,max_width=None,
        input_store = data_store,
        input_store_key=id_df,
    )
    
    
    title_row = None
    if title is not None:
        title_row = make_page_title(title,div_id=f"{dt_id}_title_row",html_container=html.H3)  
    
    # make the multi column panel for the filter row
    filter_htmls = [
#         dashapp.multi_column_panel(
        dashapp.multi_row_panel(
#             [html.Div(text_values[i]),filter_components[i]],
#             grid_template=['1fr 1fr'],parent_class=None,
            [filter_components[i]],
            grid_template=['1fr'],parent_class=None,            
        ) for i in range(len(filter_dd_list))
    ]
    
    fr_gt = [' '.join(['1fr' for _ in range(len(filter_htmls))])]
    filter_row = dashapp.multi_column_panel(
        filter_htmls,parent_class=dashapp.pn,div_id=f'{dt_id}_filter_row',
        grid_template=fr_gt
    )
    
    
    # row with dashtable
    dt_values_row = html.Div(dt_values,style={'width':'90vw'})
    # row 7 col 2
    all_rows = [filter_row,title_row,dt_values_row,data_store_loading]
    all_links = [dt_nav_link,data_store_link]
    return all_rows,all_links,
    


In [68]:
def get_cuv_imp_from_redis():
    df_cuv_imp2 = get_redis_df('df_cuv_implied')
    df_cuv_imp2['commod'] = df_cuv_imp2.symbol.str.slice(0,2)
    df_cuv_imp2['contract_year'] = df_cuv_imp2.symbol.str.slice(-2,).astype(int) + 2000
    return df_cuv_imp2
        

In [201]:
# import importlib
# importlib.reload(dashapp)

In [202]:
if __name__=='__main__':
    panel_color = '#FFFFFA'
    all_links = []    
    
    # Create an instance of DashApp, which holds all of the html and dcc elements, 
    #    as well as all of the DashLinks, and finally creates the instance of Dash.app
    dap = dashapp.DashApp()
    
    # *********** Assemble all of he rows and columns below ***************

    # ************ Create row 1 (the main title) *******************
    app_title = """Show ATM Implied Volatilities
using a
Constant Underlying Price"""
    r1 = make_page_title(app_title,div_id='r1',html_container=html.H3)                  

    # *************** Create other rows ****************************
    df_init = get_cuv_imp_from_redis()
    filter_ddd_list = [
        _FilterDescriptor('commod','CL','Commodity: '),
        _FilterDescriptor('contract_year',2020,'Contract Year: ')
    ]
    rows_2_4,all_links = create_dashtable_page(
        df_init,'df_cuv_implied',filter_ddd_list,get_cuv_imp_from_redis,
        title = "ATM Vol vs Price Data"
    )
    
       
    all_rows = html.Div([r1]+rows_2_4)

    # Add all of the DashLinks to the DashApp instance (dap)
#     pdb.set_trace()
    dap.add_links(all_links)
    # Create the dash app object by calling the create_app method of dap (the instance of DashApp)
    dap.create_app(all_rows,app_title='Constant Underlying Vol',app_port=8804)
    
    

2020-06-30 08:05:45,215 - root - DEBUG - df_cuv_implied entering create_dt_div
2020-06-30 08:05:45,229 - root - DEBUG - df_cuv_implied exiting create_dt_div
2020-06-30 08:05:45,310 - root - INFO - This app will run at the URL: http://127.0.0.1:8804


 * Serving Flask app "dashapp.dashapp2" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


2020-06-30 08:05:45,322 - werkzeug - INFO -  * Running on http://127.0.0.1:8804/ (Press CTRL+C to quit)
2020-06-30 08:05:47,683 - werkzeug - INFO - 127.0.0.1 - - [30/Jun/2020 08:05:47] "GET / HTTP/1.1" 200 -


serving -- package: dash_renderer[1.3.0] resource: polyfill@7.8.7.min.js => location: ['/Users/bperlman1/Virtualenvs3/dashrisk5/lib/python3.6/site-packages/dash_renderer']


2020-06-30 08:05:47,760 - werkzeug - INFO - 127.0.0.1 - - [30/Jun/2020 08:05:47] "GET /assets/custom.css?m=1583299996.0 HTTP/1.1" 200 -
2020-06-30 08:05:47,763 - werkzeug - INFO - 127.0.0.1 - - [30/Jun/2020 08:05:47] "GET /assets/dashapp_example_3_rows.css?m=1585932241.0 HTTP/1.1" 200 -


...

_dash_table_update_paging_closure: page_current:17 page_size: 20


2020-06-30 08:06:25,013 - werkzeug - INFO - 127.0.0.1 - - [30/Jun/2020 08:06:25] "POST /_dash-update-component HTTP/1.1" 200 -


_dash_table_update_paging_closure: page_current:29 page_size: 20


2020-06-30 08:06:32,131 - werkzeug - INFO - 127.0.0.1 - - [30/Jun/2020 08:06:32] "POST /_dash-update-component HTTP/1.1" 200 -


_dash_table_update_paging_closure: page_current:99 page_size: 20


## END

In [199]:
df_test = get_cuv_imp_from_redis()
df_test = df_test[df_test.symbol.str.slice(0,2)=='CL']


c= 'settle_date'
g = dashapp.generate_sub_dfs(df_test,c,10)
for df_sub in g:
    symbols = df_sub.symbol.unique()
    
    rows = cols = np.repeat(1,len(symbols))
    is_sec_list = [False for _ in range(len(symbols))]
    yaxis_titles = ['Implied Pseudo Vol' for _ in range(len(symbols))]
    df_figure = dashapp.create_subplot_df_figure(
        symbols,'settle_date',rows,cols,is_sec_list,yaxis_titles)
    df_sub2 = df_sub[['settle_date','symbol','iv']]
    df_sub_to_plot = dashapp.flatten_columns(df_sub2,'settle_date','symbol')
    yyyymmdd_beg = df_sub_to_plot.settle_date.min()
    yyyymmdd_end = df_sub_to_plot.settle_date.max()
    title = f'Implied Vol vs Date for all Contracts: {yyyymmdd_beg} - {yyyymmdd_end}'
    iplot(
        dashapp.plotly_subplots(
            df_sub_to_plot,
            df_figure,title=title
        )
    )

In [200]:
for gb in df_test.groupby('contract_year',as_index=False): 
#     df_sub = gb[1].style.set_caption(f"<div style='text-align:center;'>{dft[0]}</div>")
    df_sub = gb[1][['settle_date','symbol','iv']]
    year = gb[0]
    title = f'Implied Vol vs Date for all Contracts - {year}'
    df_data2 = dashapp.flatten_columns(df_sub,'settle_date','symbol')
    iplot(dashapp.plotly_plot(df_in=df_data2,x_column='settle_date',
                             plot_title=title,legend_orientation='v'))
    

In [198]:
df_test_single2 = df_test_single[['settle_date','symbol','iv']]
dashapp.flatten_columns(df_test_single2,'settle_date','symbol')

settle_date     CLG11     CLH11     CLJ11     CLK11     CLM11  CLN11  \
0       20110103  0.507499  0.500325  0.524088  0.533039  0.543616    NaN   
1       20110104  0.538744  0.521445  0.533934  0.541228  0.554119    NaN   
2       20110105  0.512729  0.503814  0.518000  0.531993  0.539425    NaN   
3       20110106  0.527733  0.512557  0.524606  0.532118  0.545413    NaN   
4       20110107  0.519928  0.511475  0.525662  0.532676  0.547302    NaN   
..           ...       ...       ...       ...       ...       ...    ...   
216     20111109       NaN       NaN       NaN       NaN       NaN    NaN   
217     20111110       NaN       NaN       NaN       NaN       NaN    NaN   
218     20111111       NaN       NaN       NaN       NaN       NaN    NaN   
219     20111114       NaN       NaN       NaN       NaN       NaN    NaN   
220     20111115       NaN       NaN       NaN       NaN       NaN    NaN   

     CLQ11  CLU11  CLV11  CLX11     CLZ11  
0      NaN    NaN    NaN    NaN       NaN  
1      NaN    NaN    NaN    NaN       NaN  
2      NaN    NaN    NaN    NaN       NaN  
3      NaN    NaN    NaN    NaN       NaN  
4      NaN    NaN    NaN    NaN       NaN  
..     ...    ...    ...    ...       ...  
216    NaN    NaN    NaN    NaN  0.736409  
217    NaN    NaN    NaN    NaN  0.670605  
218    NaN    NaN    NaN    NaN  0.567741  
219    NaN    NaN    NaN    NaN  0.514122  
220    NaN    NaN    NaN    NaN  0.048281  

[221 rows x 12 columns]